In [1]:
# encoding=utf8  
import numpy as np
import tensorflow as tf
import config
def unpickle(file):
  import _pickle as cPickle
  fo = open(file, 'rb')
  dict = cPickle.load(fo,encoding='latin1')
  fo.close()
  if 'data' in dict:
    dict['data'] = dict['data'].reshape((-1, 3, 32, 32)).swapaxes(1, 3).swapaxes(1, 2).reshape(-1, 32*32*3) / 256.

  return dict

In [2]:
def load_data_one(f):
  batch = unpickle(f)
  data = batch['data']
  labels = batch['labels']
  print ("Loading %s: %d" % (f, len(data)))
  return data, labels


In [3]:

def load_data(files, data_dir, label_count):
  data, labels = load_data_one(data_dir + '/' + files[0])
  for f in files[1:]:
    data_n, labels_n = load_data_one(data_dir + '/' + f)
    data = np.append(data, data_n, axis=0)
    labels = np.append(labels, labels_n, axis=0)
  labels = np.array([ [ float(i == label) for i in range(label_count) ] for label in labels ])
  return data, labels

In [4]:
def run_in_batch_avg(session, tensors, batch_placeholders, feed_dict={}, batch_size=200):                              
  res = [ 0 ] * len(tensors)                                                                                           
  batch_tensors = [ (placeholder, feed_dict[ placeholder ]) for placeholder in batch_placeholders ]                    
  total_size = len(batch_tensors[0][1])                                                                                
  batch_count = (total_size + batch_size - 1) / batch_size                                                             
  for batch_idx in range(batch_count):                                                                                
    current_batch_size = None                                                                                          
    for (placeholder, tensor) in batch_tensors:                                                                        
      batch_tensor = tensor[ batch_idx*batch_size : (batch_idx+1)*batch_size ]                                         
      current_batch_size = len(batch_tensor)                                                                           
      feed_dict[placeholder] = tensor[ batch_idx*batch_size : (batch_idx+1)*batch_size ]                               
    tmp = session.run(tensors, feed_dict=feed_dict)                                                                    
    res = [ r + t * current_batch_size for (r, t) in zip(res, tmp) ]                                                   
  return [ r / float(total_size) for r in res ]


In [5]:
def add_dyprune(weights):
    import config
    crate = config.crate[weights.name[:-2]]
    print(weights.name[:-2])
    prune_mask = tf.Variable(tf.ones_like(weights),name=weights.name[:-2]+'mask', trainable=False)

    mean = tf.divide(tf.reduce_sum(tf.multiply(tf.abs(weights),prune_mask)),tf.reduce_sum(prune_mask))
    
    var = tf.multiply(weights,prune_mask)
    var = tf.square(var)
    mean_q = tf.square(mean)*tf.reduce_sum(prune_mask)
    var = tf.reduce_sum(var) - mean_q
    
    var = tf.divide(var,tf.reduce_sum(prune_mask))
    var = tf.sqrt(var)
    
    t1_lower = (mean+var*crate)*0.45

    indicator_lower1 = tf.greater_equal(tf.abs(weights), tf.ones_like(weights) * t1_lower)
    
    t1_upper = (mean+var*crate)*0.55

    
    
    
    
    
    indicator_upper1 = tf.greater_equal(tf.abs(weights), tf.ones_like(weights) * t1_upper)
    indicator_matrix1 = tf.greater_equal(prune_mask, tf.zeros_like(weights))
    indicator_matrix1 = tf.logical_and(indicator_matrix1,indicator_lower1)
    indicator_matrix1 = tf.logical_or(indicator_matrix1,indicator_upper1)
    indicator_matrix1 = tf.to_float(indicator_matrix1)
    update = prune_mask.assign(indicator_matrix1)
    print(update.name)

    prune_fc = tf.multiply(weights, prune_mask)
    return prune_fc


def weight_variable(shape):
  initial = tf.truncated_normal(shape, stddev=0.01)   
  w = tf.Variable(initial)
  if w.name[:-2] in config.exc_para: w = add_dyprune(w)
  return w


def bias_variable(shape):
  initial = tf.constant(0.01, shape=shape)
  return tf.Variable(initial)

def conv2d(input, in_features, out_features, kernel_size, with_bias=False):
  W = weight_variable([ kernel_size, kernel_size, in_features, out_features ])
  conv = tf.nn.conv2d(input, W, [ 1, 1, 1, 1 ], padding='SAME')
  if with_bias:
    return conv + bias_variable([ out_features ])
  return conv

def batch_activ_conv(current, in_features, out_features, kernel_size, is_training, keep_prob):
  current = tf.contrib.layers.batch_norm(current, scale=True, is_training=is_training, updates_collections=None)
  current = tf.nn.relu(current)
  current = conv2d(current, in_features, out_features, kernel_size)
  current = tf.nn.dropout(current, keep_prob)
  return current

def block(input, layers, in_features, growth, is_training, keep_prob):
  current = input
  features = in_features
  for idx in range(layers):
    tmp = batch_activ_conv(current, features, growth, 3, is_training, keep_prob)
    current = tf.concat((current, tmp),3)
    features += growth
  return current, features

def avg_pool(input, s):
  return tf.nn.avg_pool(input, [ 1, s, s, 1 ], [1, s, s, 1 ], 'VALID')



In [6]:
data_dir = './data'
image_size = 32
image_dim = image_size * image_size * 3
# meta = unpickle(data_dir + '/batches.meta')
# label_names = meta['label_names']
# label_count = len(label_names)
label_count = 10
# train_files = [ 'data_batch_%d' % d for d in range(1, 6) ]
# train_data, train_labels = load_data(train_files, data_dir, label_count)
# pi = np.random.permutation(len(train_data))
# train_data, train_labels = train_data[pi], train_labels[pi]
# test_data, test_labels = load_data([ 'test_batch' ], data_dir, label_count)
# print ("Train:", np.shape(train_data), np.shape(train_labels))
# print ("Test:", np.shape(test_data), np.shape(test_labels))
# data = { 'train_data': train_data,
#   'train_labels': train_labels,
#   'test_data': test_data,
#   'test_labels': test_labels }
depth = 40

In [7]:

weight_decay = 1e-4
layers = int((depth - 4) / 3)


xs = tf.placeholder("float", shape=[None, image_dim])
ys = tf.placeholder("float", shape=[None, label_count])
lr = tf.placeholder("float", shape=[])
keep_prob = tf.placeholder(tf.float32)
is_training = tf.placeholder("bool", shape=[])


current = tf.reshape(xs, [ -1, 32, 32, 3 ])
current = conv2d(current, 3, 16, 3)

current, features = block(current, layers, 16, 12, is_training, keep_prob)
current = batch_activ_conv(current, features, features, 1, is_training, keep_prob)
current = avg_pool(current, 2)
current, features = block(current, layers, features, 12, is_training, keep_prob)
current = batch_activ_conv(current, features, features, 1, is_training, keep_prob)
current = avg_pool(current, 2)
current, features = block(current, layers, features, 12, is_training, keep_prob)

current = tf.contrib.layers.batch_norm(current, scale=True, is_training=is_training, updates_collections=None)
current = tf.nn.relu(current)
current = avg_pool(current, 8)
final_dim = features
current = tf.reshape(current, [ -1, final_dim ])
Wfc = weight_variable([ final_dim, label_count ])
bfc = bias_variable([ label_count ])
ys_ = tf.nn.softmax( tf.matmul(current, Wfc) + bfc )

cross_entropy = -tf.reduce_mean(ys * tf.log(ys_ + 1e-12))
l2 = tf.add_n([tf.nn.l2_loss(var) for var in tf.trainable_variables()])
train_step = tf.train.MomentumOptimizer(lr, 0.9, use_nesterov=True).minimize(cross_entropy + l2 * weight_decay)
correct_prediction = tf.equal(tf.argmax(ys_, 1), tf.argmax(ys, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))
    


Variable_2
Assign:0
Variable_3
Assign_1:0
Variable_4
Assign_2:0
Variable_5
Assign_3:0
Variable_6
Assign_4:0
Variable_7
Assign_5:0
Variable_8
Assign_6:0
Variable_9
Assign_7:0
Variable_10
Assign_8:0
Variable_11
Assign_9:0
Variable_12
Assign_10:0
Variable_14
Assign_11:0
Variable_15
Assign_12:0
Variable_16
Assign_13:0
Variable_17
Assign_14:0
Variable_18
Assign_15:0
Variable_19
Assign_16:0
Variable_20
Assign_17:0
Variable_21
Assign_18:0
Variable_22
Assign_19:0
Variable_23
Assign_20:0
Variable_24
Assign_21:0
Variable_25
Assign_22:0
Variable_27
Assign_23:0
Variable_28
Assign_24:0
Variable_29
Assign_25:0
Variable_30
Assign_26:0
Variable_31
Assign_27:0
Variable_32
Assign_28:0
Variable_33
Assign_29:0
Variable_34
Assign_30:0
Variable_35
Assign_31:0
Variable_36
Assign_32:0
Variable_37
Assign_33:0
Variable_38
Assign_34:0


In [8]:
para_dict={}
for k in tf.global_variables():
    if k not in tf.contrib.framework.get_variables_by_suffix('Momentum'):
            para_dict[k.name[:-2]] = k

In [9]:
para_toload={}
for k in tf.global_variables():
    if k not in tf.contrib.framework.get_variables_by_suffix('Momentum'):
        if 'mask' not in k.name:            
            para_toload[k.name[:-2]] = k

In [10]:
A_assign=[]
for k in tf.get_default_graph().get_operations():
    if k.name.startswith('Assign'):
        A_assign.append(k.values()[0])
update=tf.group(*A_assign)

In [15]:
sess=tf.InteractiveSession()
saver = tf.train.Saver(para_dict)
#saver = tf.train.Saver(para_dict)
saver.restore(sess,'C:/Users/lhlne/Desktop/project/densenet/dnsmodel/c29283bug/dnsc2_72.ckpt')
#saver.restore(sess,'./modellog/weightonlypara93.ckpt')

INFO:tensorflow:Restoring parameters from C:/Users/lhlne/Desktop/project/densenet/dnsmodel/c29283bug/dnsc2_72.ckpt


NotFoundError: Key Variable_2mask not found in checkpoint
	 [[Node: save_2/RestoreV2_197 = RestoreV2[dtypes=[DT_FLOAT], _device="/job:localhost/replica:0/task:0/cpu:0"](_arg_save_2/Const_0_0, save_2/RestoreV2_197/tensor_names, save_2/RestoreV2_197/shape_and_slices)]]
	 [[Node: save_2/RestoreV2_208/_61 = _Recv[client_terminated=false, recv_device="/job:localhost/replica:0/task:0/gpu:0", send_device="/job:localhost/replica:0/task:0/cpu:0", send_device_incarnation=1, tensor_name="edge_528_save_2/RestoreV2_208", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/gpu:0"]()]]

Caused by op 'save_2/RestoreV2_197', defined at:
  File "D:\Anaconda3\lib\runpy.py", line 193, in _run_module_as_main
    "__main__", mod_spec)
  File "D:\Anaconda3\lib\runpy.py", line 85, in _run_code
    exec(code, run_globals)
  File "D:\Anaconda3\lib\site-packages\ipykernel_launcher.py", line 16, in <module>
    app.launch_new_instance()
  File "D:\Anaconda3\lib\site-packages\traitlets\config\applicatio

In [14]:
total_count = 0
for k in para_dict.items():
    if 'mask' in k[0]:
        weight = np.reshape(k[1].eval(),[-1])
        total_count += len(weight[weight==0])
total_count

305427

In [12]:
# sess=tf.InteractiveSession()
# saver = tf.train.Saver(para_dict)
# saver.restore(sess,'C:/Users/lhlne/Desktop\project/densenet/dnsmodel/9276/densenetdnsfinal1st_92789_1.ckpt')

In [24]:
total_para = 0
existing_para = 0
for k in para_dict.items():
  #  if k[0] not in config.all_para:
    if 'mask' in k[0]:
        print(k[0])
        print(len(np.reshape(k[1].eval(),[-1])))
        weight = np.reshape(k[1].eval(),[-1])
        percen = (len(weight[weight == 0]))/(len(np.reshape(k[1].eval(),[-1])))
        print('zeropercen', percen)
        total_para += len(weight[weight == 0])
        #total_para += len(np.reshape(k[1].eval(),[-1]))

Variablemask
432
zeropercen 0.2152777777777778
Variable_1mask
1728
zeropercen 0.5856481481481481
Variable_2mask
3024
zeropercen 0.8551587301587301
Variable_3mask
4320
zeropercen 0.7240740740740741
Variable_4mask
5616
zeropercen 0.6834045584045584
Variable_5mask
6912
zeropercen 0.5697337962962963
Variable_6mask
8208
zeropercen 0.5370370370370371
Variable_7mask
9504
zeropercen 0.6044823232323232
Variable_8mask
10800
zeropercen 0.607037037037037
Variable_9mask
12096
zeropercen 0.6178902116402116
Variable_10mask
13392
zeropercen 0.6229091995221028
Variable_11mask
14688
zeropercen 0.5375816993464052
Variable_12mask
15984
zeropercen 0.5646271271271271
Variable_13mask
25600
zeropercen 0.3276953125
Variable_14mask
17280
zeropercen 0.5553819444444444
Variable_15mask
18576
zeropercen 0.5108742463393626
Variable_16mask
19872
zeropercen 0.5265700483091788
Variable_17mask
21168
zeropercen 0.5278722600151171
Variable_18mask
22464
zeropercen 0.5340990028490028
Variable_19mask
23760
zeropercen 0.55938

In [25]:
total_para

575418

In [20]:
total_para = 0
existing_para = 0
for k in para_dict.items():
    if 'mask' in k[0]:
        print(k[0])
        print(np.sum(k[1].eval()))
        existing_para +=np.sum(k[1].eval())
        print(len(np.reshape(k[1].eval(),[-1])))
        total_para += len(np.reshape(k[1].eval(),[-1]))
        percen = np.sum(k[1].eval())/len(np.reshape(k[1].eval(),[-1]))
        print(percen)


Variablemask


FailedPreconditionError: Attempting to use uninitialized value Variablemask
	 [[Node: Variablemask/_788 = _Send[T=DT_FLOAT, client_terminated=false, recv_device="/job:localhost/replica:0/task:0/cpu:0", send_device="/job:localhost/replica:0/task:0/gpu:0", send_device_incarnation=1, tensor_name="edge_4_Variablemask", _device="/job:localhost/replica:0/task:0/gpu:0"](Variablemask)]]
	 [[Node: Variablemask/_789 = _Recv[_start_time=0, client_terminated=false, recv_device="/job:localhost/replica:0/task:0/cpu:0", send_device="/job:localhost/replica:0/task:0/gpu:0", send_device_incarnation=1, tensor_name="edge_4_Variablemask", tensor_type=DT_FLOAT, _device="/job:localhost/replica:0/task:0/cpu:0"]()]]

In [13]:
print(total_para) 
print(existing_para) 

1001616
279479.0


In [13]:
import config


In [28]:
save_dict ={}
num_total = 0
for k in para_toload.items():
    weight = k[1].eval()
    if k[0] in config.exc_para:
        a = k[0]+'mask'
        save_dict[a] = np.nonzero(np.reshape(para_dict[a].eval(),[-1]))
        num_total += len(np.reshape(save_dict[a],[-1]))
        print(len(np.reshape(save_dict[a],[-1])))
        b = k[0]+'spar'
        save_dict[b] = np.reshape(weight,-1)[np.nonzero(np.reshape(para_dict[a].eval(),[-1]))]
        num_total += len(np.reshape(save_dict[b],[-1]))
        print(len(np.reshape(save_dict[a],[-1])))
    else:        
        save_dict[k[0]] = weight
        
save_dict
        
        

467
467
1072
1072
1400
1400
2279
2279
2706
2706
2905
2905
3231
3231
3586
3586
3734
3734
4787
4787
4888
4888
5913
5913
6605
6605
6590
6590
7119
7119
7392
7392
7399
7399
8272
8272
8539
8539
9347
9347
9766
9766
10288
10288
10313
10313
11524
11524
11941
11941
12818
12818
13189
13189
13246
13246
13094
13094
13394
13394
11054
11054
9216
9216
5078
5078
6508
6508
5801
5801


{'BatchNorm/beta': array([ 0.13457707,  0.19024231, -0.18214345, -0.1109003 ,  0.03855705,
         0.11476456,  0.06733284,  0.21596111, -0.05550055,  0.17144607,
        -0.15407375,  0.04680792,  0.27738744, -0.03944726, -0.04971396,
         0.19041337], dtype=float32),
 'BatchNorm/gamma': array([ 0.12703843,  0.25982744,  0.21970652,  0.20171469,  0.10560513,
         0.1312001 ,  0.23941629, -0.00312303,  0.14658585,  0.11787019,
         0.20863743,  0.04398109,  0.19313277,  0.01430674,  0.11291002,
         0.2223836 ], dtype=float32),
 'BatchNorm/moving_mean': array([ -6.37836335e-03,   4.00622492e-04,   2.74965577e-02,
         -3.58538106e-02,  -1.13799423e-02,  -1.52296098e-02,
         -2.37340983e-02,  -1.55452862e-02,  -2.44026501e-02,
          3.09114717e-03,  -2.89383113e-01,  -4.31017220e-01,
          8.72501172e-03,   4.77297783e-01,  -2.47517992e-02,
         -4.61144699e-03], dtype=float32),
 'BatchNorm/moving_variance': array([ 0.00881073,  0.02814272,  0.04148

In [21]:
num_total

671780

In [30]:
num_total/2

255461.0

In [25]:
save_dict ={}
num_total = 0
for k in para_toload.items():
    weight = k[1].eval()
    if k[0] in config.exc_para:
        a = k[0]+'mask'
        save_dict[k[0]] = np.multiply(para_dict[a].eval(),weight)
        num_total += len(np.reshape(weight,[-1]))
    else:        
        save_dict[k[0]] = weight
        num_total += len(np.reshape(weight,[-1]))
save_dict

{'BatchNorm/beta': array([ 0.13457707,  0.19024231, -0.18214345, -0.1109003 ,  0.03855705,
         0.11476456,  0.06733284,  0.21596111, -0.05550055,  0.17144607,
        -0.15407375,  0.04680792,  0.27738744, -0.03944726, -0.04971396,
         0.19041337], dtype=float32),
 'BatchNorm/gamma': array([ 0.12703843,  0.25982744,  0.21970652,  0.20171469,  0.10560513,
         0.1312001 ,  0.23941629, -0.00312303,  0.14658585,  0.11787019,
         0.20863743,  0.04398109,  0.19313277,  0.01430674,  0.11291002,
         0.2223836 ], dtype=float32),
 'BatchNorm/moving_mean': array([ -6.37836335e-03,   4.00622492e-04,   2.74965577e-02,
         -3.58538106e-02,  -1.13799423e-02,  -1.52296098e-02,
         -2.37340983e-02,  -1.55452862e-02,  -2.44026501e-02,
          3.09114717e-03,  -2.89383113e-01,  -4.31017220e-01,
          8.72501172e-03,   4.77297783e-01,  -2.47517992e-02,
         -4.61144699e-03], dtype=float32),
 'BatchNorm/moving_variance': array([ 0.00881073,  0.02814272,  0.04148

In [26]:
num_total

1037818

In [27]:
import pickle
# create dictC:\Users\lhlne\Desktop\project\densenet\compare\prune
# save dict
f1 = open("C:/Users/lhlne/Desktop/project/densenet/compare/dns/try.txt","wb")
pickle.dump(save_dict, f1)
f1.close()
# load dict
f2 = open("C:/Users/lhlne/Desktop/project/densenet/compare/dns/try.txt","rb")
load_list = pickle.load(f2)
f2.close()
# print 
print(load_list)

{'Variable': array([[[[  4.92111892e-01,   9.04925615e-02,  -1.15643658e-01,
            1.92748174e-01,  -7.57131726e-02,  -6.11339547e-02,
           -8.94254968e-02,   2.05577821e-01,  -2.22102995e-03,
            1.96597241e-02,   9.45127159e-02,   1.26177305e-02,
           -2.19070613e-01,   4.48347814e-02,  -8.42528194e-02,
           -8.16309676e-02],
         [ -3.81186865e-02,  -1.41345233e-01,   9.40059125e-02,
            1.84190571e-01,  -9.23852250e-02,   3.86084728e-02,
           -3.73923071e-02,   2.39260033e-01,   2.81710904e-02,
            7.98625685e-03,  -5.33886403e-02,  -2.66563483e-02,
            7.22232312e-02,   1.41467340e-02,  -1.08108066e-01,
            1.28178030e-01],
         [ -4.58505541e-01,   1.09957173e-01,   1.10009253e-01,
            1.95829362e-01,  -1.72955431e-02,   5.54604875e-03,
           -1.39967307e-01,   2.12778360e-01,   4.86635491e-02,
           -9.28955972e-02,  -8.02608207e-02,  -6.17253687e-03,
            2.17664406e-01,  -5.3

In [13]:
sess=tf.InteractiveSession()
saver = tf.train.Saver(para_toload)
saver.restore(sess,'C:/Users/lhlne/Desktop\project/densenet/modellog/weightonlypara93.ckpt')

INFO:tensorflow:Restoring parameters from C:/Users/lhlne/Desktop\project/densenet/modellog/weightonlypara93.ckpt


In [23]:
save_dict ={}
for k in para_toload.items():
    weight = k[1].eval() 
    
    save_dict[k[0]] = weight
save_dict

{'BatchNorm/beta': array([ 0.13457707,  0.19024231, -0.18214345, -0.1109003 ,  0.03855705,
         0.11476456,  0.06733284,  0.21596111, -0.05550055,  0.17144607,
        -0.15407375,  0.04680792,  0.27738744, -0.03944726, -0.04971396,
         0.19041337], dtype=float32),
 'BatchNorm/gamma': array([ 0.12703843,  0.25982744,  0.21970652,  0.20171469,  0.10560513,
         0.1312001 ,  0.23941629, -0.00312303,  0.14658585,  0.11787019,
         0.20863743,  0.04398109,  0.19313277,  0.01430674,  0.11291002,
         0.2223836 ], dtype=float32),
 'BatchNorm/moving_mean': array([ -6.37836335e-03,   4.00622492e-04,   2.74965577e-02,
         -3.58538106e-02,  -1.13799423e-02,  -1.52296098e-02,
         -2.37340983e-02,  -1.55452862e-02,  -2.44026501e-02,
          3.09114717e-03,  -2.89383113e-01,  -4.31017220e-01,
          8.72501172e-03,   4.77297783e-01,  -2.47517992e-02,
         -4.61144699e-03], dtype=float32),
 'BatchNorm/moving_variance': array([ 0.00881073,  0.02814272,  0.04148

In [15]:
import pickle
# create dictC:\Users\lhlne\Desktop\project\densenet\compare\prune
# save dict
f1 = open("C:/Users/lhlne/Desktop/project/densenet/compare/original.txt","wb")
pickle.dump(save_dict, f1)
f1.close()
# load dict
f2 = open("C:/Users/lhlne/Desktop/project/densenet/compare/original.txt","rb")
load_list = pickle.load(f2)
f2.close()
# print 
print(load_list)

{'Variable': array([[[[  3.44222993e-01,   2.52807736e-02,  -8.36442709e-02,
            1.01950161e-01,  -5.06648906e-02,  -1.10229645e-02,
           -5.23623824e-02,   1.35116205e-01,   1.07809864e-02,
            1.26128737e-02,   7.42659047e-02,   1.90676320e-02,
           -1.29201561e-01,   3.43044251e-02,  -4.21130285e-02,
           -5.40455990e-02],
         [ -4.90448661e-02,  -8.65770802e-02,   5.39431907e-02,
            9.91697311e-02,  -3.84375751e-02,   3.37356590e-02,
           -1.65567137e-02,   1.49802566e-01,   2.14102212e-02,
           -4.88093309e-03,  -3.71937118e-02,  -2.71624122e-02,
            5.00762910e-02,   1.10645629e-02,  -5.94245009e-02,
            8.37203488e-02],
         [ -2.85197020e-01,   6.44724742e-02,   6.32062480e-02,
            1.36350557e-01,  -1.73997656e-02,  -2.94546895e-02,
           -8.86704177e-02,   1.59330800e-01,   2.16072742e-02,
           -5.08017913e-02,  -4.15278710e-02,   1.50537193e-02,
            1.38265908e-01,   4.3

In [16]:
from matplotlib import pyplot as plt
for i in para_dict.items():
    if 'Variable' in i[0]:
        a = para_dict[i[0]].eval()
        b = np.reshape(a,[-1])
        c = sum(b ==0)
        d = np.shape(b)
   #     e = np.percentile(b, 75)
        print(c)
        print(d)
 #       print(e)
   #     print(int(np.log10(abs(e))))
        print('percentage',c/d)
#         print(sum(b ==0))
#         plt.hist(abs(b)) 
#         plt.title(i[0]) 
#         plt.show()

216
(432,)
percentage [ 0.5]
864
(1728,)
percentage [ 0.5]
1512
(3024,)
percentage [ 0.5]
2160
(4320,)
percentage [ 0.5]
2808
(5616,)
percentage [ 0.5]
3456
(6912,)
percentage [ 0.5]
4104
(8208,)
percentage [ 0.5]
4752
(9504,)
percentage [ 0.5]
5400
(10800,)
percentage [ 0.5]
6048
(12096,)
percentage [ 0.5]
6696
(13392,)
percentage [ 0.5]
7344
(14688,)
percentage [ 0.5]
7992
(15984,)
percentage [ 0.5]
12800
(25600,)
percentage [ 0.5]
8640
(17280,)
percentage [ 0.5]
9288
(18576,)
percentage [ 0.5]
9936
(19872,)
percentage [ 0.5]
10584
(21168,)
percentage [ 0.5]
11232
(22464,)
percentage [ 0.5]
11880
(23760,)
percentage [ 0.5]
12528
(25056,)
percentage [ 0.5]
13176
(26352,)
percentage [ 0.5]
13824
(27648,)
percentage [ 0.5]
14472
(28944,)
percentage [ 0.5]
15120
(30240,)
percentage [ 0.5]
15768
(31536,)
percentage [ 0.5]
46208
(92416,)
percentage [ 0.5]
16416
(32832,)
percentage [ 0.5]
17064
(34128,)
percentage [ 0.5]
17712
(35424,)
percentage [ 0.5]
18360
(36720,)
percentage [ 0.5]
1900

In [45]:
a = parm_dict['Variable_39'].eval()
b = np.reshape(a,[-1])
print(sum(b <=0.00001))
print(np.shape(b))
print('percentage',a/b)

(4480,)

In [27]:
parm_dict={}
for k in tf.trainable_variables():
    parm_dict[k.name] = k
with tf.Session(graph=graph) as session:
    saver= tf.train.Saver(parm_dict) 
    saver.restore(session,"weights_densenet")

Variable:0
BatchNorm/beta:0
BatchNorm/gamma:0
Variable_1:0
BatchNorm_1/beta:0
BatchNorm_1/gamma:0
Variable_2:0
BatchNorm_2/beta:0
BatchNorm_2/gamma:0
Variable_3:0
BatchNorm_3/beta:0
BatchNorm_3/gamma:0
Variable_4:0
BatchNorm_4/beta:0
BatchNorm_4/gamma:0
Variable_5:0
BatchNorm_5/beta:0
BatchNorm_5/gamma:0
Variable_6:0
BatchNorm_6/beta:0
BatchNorm_6/gamma:0
Variable_7:0
BatchNorm_7/beta:0
BatchNorm_7/gamma:0
Variable_8:0
BatchNorm_8/beta:0
BatchNorm_8/gamma:0
Variable_9:0
BatchNorm_9/beta:0
BatchNorm_9/gamma:0
Variable_10:0
BatchNorm_10/beta:0
BatchNorm_10/gamma:0
Variable_11:0
BatchNorm_11/beta:0
BatchNorm_11/gamma:0
Variable_12:0
BatchNorm_12/beta:0
BatchNorm_12/gamma:0
Variable_13:0
BatchNorm_13/beta:0
BatchNorm_13/gamma:0
Variable_14:0
BatchNorm_14/beta:0
BatchNorm_14/gamma:0
Variable_15:0
BatchNorm_15/beta:0
BatchNorm_15/gamma:0
Variable_16:0
BatchNorm_16/beta:0
BatchNorm_16/gamma:0
Variable_17:0
BatchNorm_17/beta:0
BatchNorm_17/gamma:0
Variable_18:0
BatchNorm_18/beta:0
BatchNorm_18

In [7]:
depth = 40
weight_decay = 1e-4
layers = int((depth - 4) / 3)

xs = tf.placeholder("float", shape=[None, image_dim])
ys = tf.placeholder("float", shape=[None, label_count])
lr = tf.placeholder("float", shape=[])
keep_prob = tf.placeholder(tf.float32)
is_training = tf.placeholder("bool", shape=[])


current = tf.reshape(xs, [ -1, 32, 32, 3 ])
current = conv2d(current, 3, 16, 3)

current, features = block(current, layers, 16, 12, is_training, keep_prob)
current = batch_activ_conv(current, features, features, 1, is_training, keep_prob)
current = avg_pool(current, 2)
current, features = block(current, layers, features, 12, is_training, keep_prob)
current = batch_activ_conv(current, features, features, 1, is_training, keep_prob)
current = avg_pool(current, 2)
current, features = block(current, layers, features, 12, is_training, keep_prob)

current = tf.contrib.layers.batch_norm(current, scale=True, is_training=is_training, updates_collections=None)
current = tf.nn.relu(current)
current = avg_pool(current, 8)
final_dim = features
current = tf.reshape(current, [ -1, final_dim ])
Wfc = weight_variable([ final_dim, label_count ])
bfc = bias_variable([ label_count ])
ys_ = tf.nn.softmax( tf.matmul(current, Wfc) + bfc )

cross_entropy = -tf.reduce_mean(ys * tf.log(ys_ + 1e-12))
l2 = tf.add_n([tf.nn.l2_loss(var) for var in tf.trainable_variables()])
train_step = tf.train.MomentumOptimizer(lr, 0.9, use_nesterov=True).minimize(cross_entropy + l2 * weight_decay)
correct_prediction = tf.equal(tf.argmax(ys_, 1), tf.argmax(ys, 1))
accuracy = tf.reduce_mean(tf.cast(correct_prediction, "float"))

sess = tf.Session()
batch_size = 64
learning_rate = 0.1
tf.global_variables_initializer()
    # saver = tf.train.Saver()
    # train_data, train_labels = data['train_data'], data['train_labels']
    # batch_count = int(len(train_data) / batch_size)
    # batches_data = np.split(train_data[:batch_count * batch_size], batch_count)
    # batches_labels = np.split(train_labels[:batch_count * batch_size], batch_count)
    # print ("Batch per epoch: ", batch_count)
    # for epoch in range(1, 1+300):
    #   if epoch == 150: learning_rate = 0.01
    #   if epoch == 225: learning_rate = 0.001
    #   for batch_idx in range(batch_count):
    #     xs_, ys_ = batches_data[batch_idx], batches_labels[batch_idx]
    #     batch_res = session.run([ train_step, cross_entropy, accuracy ],
    #       feed_dict = { xs: xs_, ys: ys_, lr: learning_rate, is_training: True, keep_prob: 0.8 })
    #     if batch_idx % 100 == 0: print (epoch, batch_idx, batch_res[1:])

    #   save_path = saver.save(session, 'densenet_%d.ckpt' % epoch)
    #   test_results = run_in_batch_avg(session, [ cross_entropy, accuracy ], [ xs, ys ],
    #       feed_dict = { xs: data['test_data'], ys: data['test_labels'], is_training: False, keep_prob: 1. })
    #   print (epoch, batch_res[1:], test_results)


<tf.Operation 'init' type=NoOp>